In [80]:
%matplotlib inline
import pandas as pd
import numpy as np
from IPython.core.interactiveshell import InteractiveShell
import random
InteractiveShell.ast_node_interactivity = "all"
import os
from datetime import datetime
import matplotlib.pyplot as plt
import plotly.express as px
import glob
from tqdm import tqdm

import plotly.figure_factory as ff
import plotly.express as px

In [81]:
!ls -lah ../dataset

total 1588800
drwxr-xr-x  6 bhavya  staff   192B Mar 13 10:14 .
drwxr-xr-x@ 5 bhavya  staff   160B Mar 13 10:14 ..
-rw-rw-r--@ 1 bhavya  staff    54M Mar 27  2022 ca_daily_fire_2000_03252022.csv
-rw-rw-r--@ 1 bhavya  staff    14M Mar 27  2022 ca_daily_fire_2000_2021-v2.csv
-rw-rw-r--@ 1 bhavya  staff    58M Mar 27  2022 ca_daily_fire_2000_2021.csv
-rw-rw-r--@ 1 bhavya  staff   650M Mar 27  2022 usa_daily_fire_2000_march25-2022-raw.csv


In [82]:
folder = '../dataset/'
source = 'ca_daily_fire_2000_03252022.csv'
data_source = folder + source 

In [83]:
!head $data_source

latitude,longitude,acq_date,satellite,instrument,confidence,year,month
32.35334,-114.76826,2022-03-23,Aqua,MODIS,80,2022,3
32.35882,-114.76273,2022-03-24,N,VIIRS,50,2022,3
32.35924,-114.76539,2022-03-24,N,VIIRS,50,2022,3
32.36003,-114.75967,2022-03-23,N,VIIRS,50,2022,3
32.36036,-114.75935,2022-03-23,N,VIIRS,50,2022,3
32.36058,-114.7627,2022-03-22,1,VIIRS,50,2022,3
32.36094,-114.76494,2022-03-24,N,VIIRS,50,2022,3
32.36101,-114.76301,2022-03-24,1,VIIRS,50,2022,3
32.3622,-114.76353,2022-03-23,N,VIIRS,50,2022,3


In [84]:
ca_fire_df = pd.read_csv(data_source, parse_dates=['acq_date'])

In [85]:
ca_fire_df['acq_date'].min()

Timestamp('2000-11-01 00:00:00')

In [86]:
ca_fire_df['acq_date'].max()

Timestamp('2022-03-25 00:00:00')

In [87]:
ca_fire_df.shape

(1116861, 8)

In [88]:
ca_fire_df.sample(10)

latitude   longitude   acq_date satellite instrument  confidence  \
1036616  41.587753 -121.973885 2021-08-07         N      VIIRS          50   
846184   40.564178 -122.500397 2018-07-27         N      VIIRS          50   
794790   40.307529 -120.795433 2021-08-11         N      VIIRS          50   
332084   37.351925 -121.622231 2020-08-20         N      VIIRS          50   
514119   38.754398 -119.578880 2021-07-22         N      VIIRS          50   
978626   41.206867 -114.012024 2012-07-12         N      VIIRS          50   
506363   38.717262 -120.451973 2021-08-18         N      VIIRS          50   
273893   36.827900 -119.960600 2020-03-04      Aqua      MODIS          76   
133535   35.373211 -119.287285 2017-03-30         N      VIIRS          50   
298481   37.145222 -121.377296 2020-08-23         N      VIIRS          50   

         year  month  
1036616  2021      8  
846184   2018      7  
794790   2021      8  
332084   2020      8  
514119   2021      7  
978626   2012      7  
506363   2021      8  
273893   2020      3  
133535   2017      3  
298481   2020      8

In [89]:
PRECISION = 1

In [90]:
ca_fire_df.latitude = ca_fire_df.latitude.round(PRECISION)
ca_fire_df.longitude = ca_fire_df.longitude.round(PRECISION)

In [91]:
ca_fire_df

latitude  longitude   acq_date satellite instrument  confidence  \
0            32.4     -114.8 2022-03-23      Aqua      MODIS          80   
1            32.4     -114.8 2022-03-24         N      VIIRS          50   
2            32.4     -114.8 2022-03-24         N      VIIRS          50   
3            32.4     -114.8 2022-03-23         N      VIIRS          50   
4            32.4     -114.8 2022-03-23         N      VIIRS          50   
...           ...        ...        ...       ...        ...         ...   
1116856      42.0     -120.7 2012-08-14         N      VIIRS          50   
1116857      42.0     -123.6 2020-09-20         N      VIIRS          50   
1116858      42.0     -122.6 2018-07-08         N      VIIRS          50   
1116859      42.0     -120.6 2012-08-14         N      VIIRS          50   
1116860      42.0     -123.6 2020-09-11         N      VIIRS          50   

         year  month  
0        2022      3  
1        2022      3  
2        2022      3  
3        2022      3  
4        2022      3  
...       ...    ...  
1116856  2012      8  
1116857  2020      9  
1116858  2018      7  
1116859  2012      8  
1116860  2020      9  

[1116861 rows x 8 columns]

In [92]:
t_fires = ca_fire_df.groupby(['latitude', 'longitude', 'year','month']).size().reset_index()

In [93]:
t_fires

latitude  longitude  year  month   0
0          32.4     -117.1  2022      1   3
1          32.4     -117.1  2022      3  14
2          32.4     -116.9  2022      1   5
3          32.4     -116.9  2022      2   9
4          32.4     -116.9  2022      3   2
...         ...        ...   ...    ...  ..
58026      42.0     -114.1  2012      8   7
58027      42.0     -114.1  2019      8   3
58028      42.0     -114.0  2007      7   5
58029      42.0     -114.0  2013      7   4
58030      42.0     -114.0  2018      4   1

[58031 rows x 5 columns]

In [94]:
t_fires.columns = ['latitude', 'longitude', 'year','month', 'fire_count']

In [95]:
t_fires.shape

(58031, 5)

In [96]:
t_fires.sample(10)

latitude  longitude  year  month  fire_count
47874      39.7     -122.0  2019      4           7
24348      37.1     -120.3  2018      5           2
16378      36.2     -120.2  2013      2           8
7812       34.2     -117.8  2016      4           7
25259      37.2     -120.2  2015     11           1
9371       34.4     -116.9  2021      6          12
11889      35.3     -119.5  2009     10           1
54629      41.2     -122.0  2013     12           5
18784      36.5     -119.9  2013      1           4
33003      38.1     -120.5  2020      2           1

In [97]:
t_fires.nunique()

latitude       97
longitude     101
year           23
month          12
fire_count    866
dtype: int64

In [98]:
t_fires.isna().sum()

latitude      0
longitude     0
year          0
month         0
fire_count    0
dtype: int64

In [99]:
fire_loc_coords = t_fires[['latitude', 'longitude']].drop_duplicates()

In [100]:
fire_loc_coords

latitude  longitude
0          32.4     -117.1
2          32.4     -116.9
5          32.4     -114.9
7          32.4     -114.8
10         32.4     -114.6
...         ...        ...
58022      42.0     -114.5
58023      42.0     -114.4
58024      42.0     -114.2
58025      42.0     -114.1
58028      42.0     -114.0

[4914 rows x 2 columns]

In [101]:
fire_times = t_fires[['year', 'month']].drop_duplicates()

In [102]:
fire_times

year  month
0     2022      1
1     2022      3
3     2022      2
10    2014      6
14    2003      1
...    ...    ...
3450  2009      9
3764  2001     11
4085  2001      5
4168  2010     10
7110  2010      4

[257 rows x 2 columns]

In [103]:
fire_loc_coords['common_feature'] = 1
fire_times['common_feature'] = 1

In [104]:
fire_loc_coords

latitude  longitude  common_feature
0          32.4     -117.1               1
2          32.4     -116.9               1
5          32.4     -114.9               1
7          32.4     -114.8               1
10         32.4     -114.6               1
...         ...        ...             ...
58022      42.0     -114.5               1
58023      42.0     -114.4               1
58024      42.0     -114.2               1
58025      42.0     -114.1               1
58028      42.0     -114.0               1

[4914 rows x 3 columns]

In [105]:
fire_times

year  month  common_feature
0     2022      1               1
1     2022      3               1
3     2022      2               1
10    2014      6               1
14    2003      1               1
...    ...    ...             ...
3450  2009      9               1
3764  2001     11               1
4085  2001      5               1
4168  2010     10               1
7110  2010      4               1

[257 rows x 3 columns]

In [106]:
base = pd.merge(fire_loc_coords, fire_times, how='outer', on='common_feature')

In [107]:
base

latitude  longitude  common_feature  year  month
0            32.4     -117.1               1  2022      1
1            32.4     -117.1               1  2022      3
2            32.4     -117.1               1  2022      2
3            32.4     -117.1               1  2014      6
4            32.4     -117.1               1  2003      1
...           ...        ...             ...   ...    ...
1262893      42.0     -114.0               1  2009      9
1262894      42.0     -114.0               1  2001     11
1262895      42.0     -114.0               1  2001      5
1262896      42.0     -114.0               1  2010     10
1262897      42.0     -114.0               1  2010      4

[1262898 rows x 5 columns]

In [108]:
t_fires

latitude  longitude  year  month  fire_count
0          32.4     -117.1  2022      1           3
1          32.4     -117.1  2022      3          14
2          32.4     -116.9  2022      1           5
3          32.4     -116.9  2022      2           9
4          32.4     -116.9  2022      3           2
...         ...        ...   ...    ...         ...
58026      42.0     -114.1  2012      8           7
58027      42.0     -114.1  2019      8           3
58028      42.0     -114.0  2007      7           5
58029      42.0     -114.0  2013      7           4
58030      42.0     -114.0  2018      4           1

[58031 rows x 5 columns]

In [109]:
history = base.merge(t_fires, how='left', on=['latitude','longitude','year','month'])

In [110]:
history

latitude  longitude  common_feature  year  month  fire_count
0            32.4     -117.1               1  2022      1         3.0
1            32.4     -117.1               1  2022      3        14.0
2            32.4     -117.1               1  2022      2         NaN
3            32.4     -117.1               1  2014      6         NaN
4            32.4     -117.1               1  2003      1         NaN
...           ...        ...             ...   ...    ...         ...
1262893      42.0     -114.0               1  2009      9         NaN
1262894      42.0     -114.0               1  2001     11         NaN
1262895      42.0     -114.0               1  2001      5         NaN
1262896      42.0     -114.0               1  2010     10         NaN
1262897      42.0     -114.0               1  2010      4         NaN

[1262898 rows x 6 columns]

In [111]:
history['fire_count'].isna().sum()

1204867

In [112]:
history = history.fillna(0)

In [113]:
history

latitude  longitude  common_feature  year  month  fire_count
0            32.4     -117.1               1  2022      1         3.0
1            32.4     -117.1               1  2022      3        14.0
2            32.4     -117.1               1  2022      2         0.0
3            32.4     -117.1               1  2014      6         0.0
4            32.4     -117.1               1  2003      1         0.0
...           ...        ...             ...   ...    ...         ...
1262893      42.0     -114.0               1  2009      9         0.0
1262894      42.0     -114.0               1  2001     11         0.0
1262895      42.0     -114.0               1  2001      5         0.0
1262896      42.0     -114.0               1  2010     10         0.0
1262897      42.0     -114.0               1  2010      4         0.0

[1262898 rows x 6 columns]

In [114]:
history.fire_count.value_counts().head()

fire_count
0.0    1204867
1.0      21714
2.0      10234
3.0       5382
4.0       3615
Name: count, dtype: int64

In [115]:
MIN_FIRE_RECORDS = 1

In [116]:
history['fire'] = 1 * (history['fire_count'] >= MIN_FIRE_RECORDS)

In [117]:
history.shape

(1262898, 7)

In [118]:
history

latitude  longitude  common_feature  year  month  fire_count  fire
0            32.4     -117.1               1  2022      1         3.0     1
1            32.4     -117.1               1  2022      3        14.0     1
2            32.4     -117.1               1  2022      2         0.0     0
3            32.4     -117.1               1  2014      6         0.0     0
4            32.4     -117.1               1  2003      1         0.0     0
...           ...        ...             ...   ...    ...         ...   ...
1262893      42.0     -114.0               1  2009      9         0.0     0
1262894      42.0     -114.0               1  2001     11         0.0     0
1262895      42.0     -114.0               1  2001      5         0.0     0
1262896      42.0     -114.0               1  2010     10         0.0     0
1262897      42.0     -114.0               1  2010      4         0.0     0

[1262898 rows x 7 columns]

In [119]:
history['fire'].value_counts()

fire
0    1204867
1      58031
Name: count, dtype: int64

In [120]:
history.mean()

latitude            38.167847
longitude         -119.069373
common_feature       1.000000
year              2011.042802
month                6.486381
fire_count           0.884364
fire                 0.045951
dtype: float64

In [121]:
yearly = history.groupby(
    ['latitude', 'longitude', 'year'])[['fire_count', 'fire']].mean().reset_index()

In [122]:
yearly

latitude  longitude  year  fire_count      fire
0           32.4     -117.1  2000    0.000000  0.000000
1           32.4     -117.1  2001    0.000000  0.000000
2           32.4     -117.1  2002    0.000000  0.000000
3           32.4     -117.1  2003    0.000000  0.000000
4           32.4     -117.1  2004    0.000000  0.000000
...          ...        ...   ...         ...       ...
113017      42.0     -114.0  2018    0.083333  0.083333
113018      42.0     -114.0  2019    0.000000  0.000000
113019      42.0     -114.0  2020    0.000000  0.000000
113020      42.0     -114.0  2021    0.000000  0.000000
113021      42.0     -114.0  2022    0.000000  0.000000

[113022 rows x 5 columns]

In [123]:
monthly = history.groupby(
    ['latitude', 'longitude', 'year', 'month'])[['fire_count', 'fire']].mean().reset_index()

In [124]:
monthly

latitude  longitude  year  month  fire_count  fire
0            32.4     -117.1  2000     11         0.0   0.0
1            32.4     -117.1  2000     12         0.0   0.0
2            32.4     -117.1  2001      1         0.0   0.0
3            32.4     -117.1  2001      2         0.0   0.0
4            32.4     -117.1  2001      3         0.0   0.0
...           ...        ...   ...    ...         ...   ...
1262893      42.0     -114.0  2021     11         0.0   0.0
1262894      42.0     -114.0  2021     12         0.0   0.0
1262895      42.0     -114.0  2022      1         0.0   0.0
1262896      42.0     -114.0  2022      2         0.0   0.0
1262897      42.0     -114.0  2022      3         0.0   0.0

[1262898 rows x 6 columns]

In [125]:
last_year = yearly.copy()
last_year.year += 1

In [126]:
last_year

latitude  longitude  year  fire_count      fire
0           32.4     -117.1  2001    0.000000  0.000000
1           32.4     -117.1  2002    0.000000  0.000000
2           32.4     -117.1  2003    0.000000  0.000000
3           32.4     -117.1  2004    0.000000  0.000000
4           32.4     -117.1  2005    0.000000  0.000000
...          ...        ...   ...         ...       ...
113017      42.0     -114.0  2019    0.083333  0.083333
113018      42.0     -114.0  2020    0.000000  0.000000
113019      42.0     -114.0  2021    0.000000  0.000000
113020      42.0     -114.0  2022    0.000000  0.000000
113021      42.0     -114.0  2023    0.000000  0.000000

[113022 rows x 5 columns]

In [127]:
last_year.columns = ['latitude', 'longitude', 'year', 'fire_cnt_last_year', 'fire_last_year']
last_year.head(10)

latitude  longitude  year  fire_cnt_last_year  fire_last_year
0      32.4     -117.1  2001                 0.0             0.0
1      32.4     -117.1  2002                 0.0             0.0
2      32.4     -117.1  2003                 0.0             0.0
3      32.4     -117.1  2004                 0.0             0.0
4      32.4     -117.1  2005                 0.0             0.0
5      32.4     -117.1  2006                 0.0             0.0
6      32.4     -117.1  2007                 0.0             0.0
7      32.4     -117.1  2008                 0.0             0.0
8      32.4     -117.1  2009                 0.0             0.0
9      32.4     -117.1  2010                 0.0             0.0

In [128]:
last_year_month = monthly.copy()
last_year_month.year += 1
last_year_month.columns = ['latitude', 'longitude', 'year', 'month', 'fire_cnt_last_year_same_month', 'fire_last_year_same_month']
last_year_month.head(10)

latitude  longitude  year  month  fire_cnt_last_year_same_month  \
0      32.4     -117.1  2001     11                            0.0   
1      32.4     -117.1  2001     12                            0.0   
2      32.4     -117.1  2002      1                            0.0   
3      32.4     -117.1  2002      2                            0.0   
4      32.4     -117.1  2002      3                            0.0   
5      32.4     -117.1  2002      4                            0.0   
6      32.4     -117.1  2002      5                            0.0   
7      32.4     -117.1  2002      6                            0.0   
8      32.4     -117.1  2002      7                            0.0   
9      32.4     -117.1  2002      8                            0.0   

   fire_last_year_same_month  
0                        0.0  
1                        0.0  
2                        0.0  
3                        0.0  
4                        0.0  
5                        0.0  
6                        0.0  
7                        0.0  
8                        0.0  
9                        0.0

In [129]:
past = yearly.copy()
past['common_feature'] = 1

In [130]:
past

latitude  longitude  year  fire_count      fire  common_feature
0           32.4     -117.1  2000    0.000000  0.000000               1
1           32.4     -117.1  2001    0.000000  0.000000               1
2           32.4     -117.1  2002    0.000000  0.000000               1
3           32.4     -117.1  2003    0.000000  0.000000               1
4           32.4     -117.1  2004    0.000000  0.000000               1
...          ...        ...   ...         ...       ...             ...
113017      42.0     -114.0  2018    0.083333  0.083333               1
113018      42.0     -114.0  2019    0.000000  0.000000               1
113019      42.0     -114.0  2020    0.000000  0.000000               1
113020      42.0     -114.0  2021    0.000000  0.000000               1
113021      42.0     -114.0  2022    0.000000  0.000000               1

[113022 rows x 6 columns]

In [131]:
history

latitude  longitude  common_feature  year  month  fire_count  fire
0            32.4     -117.1               1  2022      1         3.0     1
1            32.4     -117.1               1  2022      3        14.0     1
2            32.4     -117.1               1  2022      2         0.0     0
3            32.4     -117.1               1  2014      6         0.0     0
4            32.4     -117.1               1  2003      1         0.0     0
...           ...        ...             ...   ...    ...         ...   ...
1262893      42.0     -114.0               1  2009      9         0.0     0
1262894      42.0     -114.0               1  2001     11         0.0     0
1262895      42.0     -114.0               1  2001      5         0.0     0
1262896      42.0     -114.0               1  2010     10         0.0     0
1262897      42.0     -114.0               1  2010      4         0.0     0

[1262898 rows x 7 columns]

In [132]:
past = history[['latitude', 'longitude', 'year', 'common_feature']].drop_duplicates().merge(
    past, on=['latitude', 'longitude',  'common_feature'])

In [133]:
past

latitude  longitude  year_x  common_feature  year_y  fire_count  \
0            32.4     -117.1    2022               1    2000    0.000000   
1            32.4     -117.1    2022               1    2001    0.000000   
2            32.4     -117.1    2022               1    2002    0.000000   
3            32.4     -117.1    2022               1    2003    0.000000   
4            32.4     -117.1    2022               1    2004    0.000000   
...           ...        ...     ...             ...     ...         ...   
2599501      42.0     -114.0    2000               1    2018    0.083333   
2599502      42.0     -114.0    2000               1    2019    0.000000   
2599503      42.0     -114.0    2000               1    2020    0.000000   
2599504      42.0     -114.0    2000               1    2021    0.000000   
2599505      42.0     -114.0    2000               1    2022    0.000000   

             fire  
0        0.000000  
1        0.000000  
2        0.000000  
3        0.000000  
4        0.000000  
...           ...  
2599501  0.083333  
2599502  0.000000  
2599503  0.000000  
2599504  0.000000  
2599505  0.000000  

[2599506 rows x 7 columns]

In [134]:
past = past[past.year_x < past.year_y]

In [135]:
past

latitude  longitude  year_x  common_feature  year_y  fire_count  \
38           32.4     -117.1    2014               1    2015    0.000000   
39           32.4     -117.1    2014               1    2016    0.000000   
40           32.4     -117.1    2014               1    2017    0.000000   
41           32.4     -117.1    2014               1    2018    0.000000   
42           32.4     -117.1    2014               1    2019    0.000000   
...           ...        ...     ...             ...     ...         ...   
2599501      42.0     -114.0    2000               1    2018    0.083333   
2599502      42.0     -114.0    2000               1    2019    0.000000   
2599503      42.0     -114.0    2000               1    2020    0.000000   
2599504      42.0     -114.0    2000               1    2021    0.000000   
2599505      42.0     -114.0    2000               1    2022    0.000000   

             fire  
38       0.000000  
39       0.000000  
40       0.000000  
41       0.000000  
42       0.000000  
...           ...  
2599501  0.083333  
2599502  0.000000  
2599503  0.000000  
2599504  0.000000  
2599505  0.000000  

[1243242 rows x 7 columns]

In [136]:
past = past.groupby(['latitude', 'longitude', 'year_y'])[['fire_count', 'fire']].mean().reset_index()


In [137]:
past

latitude  longitude  year_y  fire_count      fire
0           32.4     -117.1    2001    0.000000  0.000000
1           32.4     -117.1    2002    0.000000  0.000000
2           32.4     -117.1    2003    0.000000  0.000000
3           32.4     -117.1    2004    0.000000  0.000000
4           32.4     -117.1    2005    0.000000  0.000000
...          ...        ...     ...         ...       ...
108103      42.0     -114.0    2018    0.083333  0.083333
108104      42.0     -114.0    2019    0.000000  0.000000
108105      42.0     -114.0    2020    0.000000  0.000000
108106      42.0     -114.0    2021    0.000000  0.000000
108107      42.0     -114.0    2022    0.000000  0.000000

[108108 rows x 5 columns]

In [138]:
past.columns = ['latitude', 'longitude', 'year', 'fire_cnt_before', 'fire_before']

In [139]:
past

latitude  longitude  year  fire_cnt_before  fire_before
0           32.4     -117.1  2001         0.000000     0.000000
1           32.4     -117.1  2002         0.000000     0.000000
2           32.4     -117.1  2003         0.000000     0.000000
3           32.4     -117.1  2004         0.000000     0.000000
4           32.4     -117.1  2005         0.000000     0.000000
...          ...        ...   ...              ...          ...
108103      42.0     -114.0  2018         0.083333     0.083333
108104      42.0     -114.0  2019         0.000000     0.000000
108105      42.0     -114.0  2020         0.000000     0.000000
108106      42.0     -114.0  2021         0.000000     0.000000
108107      42.0     -114.0  2022         0.000000     0.000000

[108108 rows x 5 columns]

In [140]:
history

latitude  longitude  common_feature  year  month  fire_count  fire
0            32.4     -117.1               1  2022      1         3.0     1
1            32.4     -117.1               1  2022      3        14.0     1
2            32.4     -117.1               1  2022      2         0.0     0
3            32.4     -117.1               1  2014      6         0.0     0
4            32.4     -117.1               1  2003      1         0.0     0
...           ...        ...             ...   ...    ...         ...   ...
1262893      42.0     -114.0               1  2009      9         0.0     0
1262894      42.0     -114.0               1  2001     11         0.0     0
1262895      42.0     -114.0               1  2001      5         0.0     0
1262896      42.0     -114.0               1  2010     10         0.0     0
1262897      42.0     -114.0               1  2010      4         0.0     0

[1262898 rows x 7 columns]

In [141]:
past

latitude  longitude  year  fire_cnt_before  fire_before
0           32.4     -117.1  2001         0.000000     0.000000
1           32.4     -117.1  2002         0.000000     0.000000
2           32.4     -117.1  2003         0.000000     0.000000
3           32.4     -117.1  2004         0.000000     0.000000
4           32.4     -117.1  2005         0.000000     0.000000
...          ...        ...   ...              ...          ...
108103      42.0     -114.0  2018         0.083333     0.083333
108104      42.0     -114.0  2019         0.000000     0.000000
108105      42.0     -114.0  2020         0.000000     0.000000
108106      42.0     -114.0  2021         0.000000     0.000000
108107      42.0     -114.0  2022         0.000000     0.000000

[108108 rows x 5 columns]

In [142]:
X = history.merge(past, how='left', on=['latitude', 'longitude', 'year'])


In [143]:
X

latitude  longitude  common_feature  year  month  fire_count  fire  \
0            32.4     -117.1               1  2022      1         3.0     1   
1            32.4     -117.1               1  2022      3        14.0     1   
2            32.4     -117.1               1  2022      2         0.0     0   
3            32.4     -117.1               1  2014      6         0.0     0   
4            32.4     -117.1               1  2003      1         0.0     0   
...           ...        ...             ...   ...    ...         ...   ...   
1262893      42.0     -114.0               1  2009      9         0.0     0   
1262894      42.0     -114.0               1  2001     11         0.0     0   
1262895      42.0     -114.0               1  2001      5         0.0     0   
1262896      42.0     -114.0               1  2010     10         0.0     0   
1262897      42.0     -114.0               1  2010      4         0.0     0   

         fire_cnt_before  fire_before  
0               5.666667     0.666667  
1               5.666667     0.666667  
2               5.666667     0.666667  
3               0.000000     0.000000  
4               0.000000     0.000000  
...                  ...          ...  
1262893         0.000000     0.000000  
1262894         0.000000     0.000000  
1262895         0.000000     0.000000  
1262896         0.000000     0.000000  
1262897         0.000000     0.000000  

[1262898 rows x 9 columns]

In [144]:
last_year

latitude  longitude  year  fire_cnt_last_year  fire_last_year
0           32.4     -117.1  2001            0.000000        0.000000
1           32.4     -117.1  2002            0.000000        0.000000
2           32.4     -117.1  2003            0.000000        0.000000
3           32.4     -117.1  2004            0.000000        0.000000
4           32.4     -117.1  2005            0.000000        0.000000
...          ...        ...   ...                 ...             ...
113017      42.0     -114.0  2019            0.083333        0.083333
113018      42.0     -114.0  2020            0.000000        0.000000
113019      42.0     -114.0  2021            0.000000        0.000000
113020      42.0     -114.0  2022            0.000000        0.000000
113021      42.0     -114.0  2023            0.000000        0.000000

[113022 rows x 5 columns]

In [145]:
X = X.merge(last_year, how='left', on=['latitude', 'longitude', 'year'])
X

latitude  longitude  common_feature  year  month  fire_count  fire  \
0            32.4     -117.1               1  2022      1         3.0     1   
1            32.4     -117.1               1  2022      3        14.0     1   
2            32.4     -117.1               1  2022      2         0.0     0   
3            32.4     -117.1               1  2014      6         0.0     0   
4            32.4     -117.1               1  2003      1         0.0     0   
...           ...        ...             ...   ...    ...         ...   ...   
1262893      42.0     -114.0               1  2009      9         0.0     0   
1262894      42.0     -114.0               1  2001     11         0.0     0   
1262895      42.0     -114.0               1  2001      5         0.0     0   
1262896      42.0     -114.0               1  2010     10         0.0     0   
1262897      42.0     -114.0               1  2010      4         0.0     0   

         fire_cnt_before  fire_before  fire_cnt_last_year  fire_last_year  
0               5.666667     0.666667                 0.0             0.0  
1               5.666667     0.666667                 0.0             0.0  
2               5.666667     0.666667                 0.0             0.0  
3               0.000000     0.000000                 0.0             0.0  
4               0.000000     0.000000                 0.0             0.0  
...                  ...          ...                 ...             ...  
1262893         0.000000     0.000000                 0.0             0.0  
1262894         0.000000     0.000000                 0.0             0.0  
1262895         0.000000     0.000000                 0.0             0.0  
1262896         0.000000     0.000000                 0.0             0.0  
1262897         0.000000     0.000000                 0.0             0.0  

[1262898 rows x 11 columns]

In [146]:
X = X.merge(last_year_month, how='left', on=['latitude', 'longitude', 'year', 'month'])
X

latitude  longitude  common_feature  year  month  fire_count  fire  \
0            32.4     -117.1               1  2022      1         3.0     1   
1            32.4     -117.1               1  2022      3        14.0     1   
2            32.4     -117.1               1  2022      2         0.0     0   
3            32.4     -117.1               1  2014      6         0.0     0   
4            32.4     -117.1               1  2003      1         0.0     0   
...           ...        ...             ...   ...    ...         ...   ...   
1262893      42.0     -114.0               1  2009      9         0.0     0   
1262894      42.0     -114.0               1  2001     11         0.0     0   
1262895      42.0     -114.0               1  2001      5         0.0     0   
1262896      42.0     -114.0               1  2010     10         0.0     0   
1262897      42.0     -114.0               1  2010      4         0.0     0   

         fire_cnt_before  fire_before  fire_cnt_last_year  fire_last_year  \
0               5.666667     0.666667                 0.0             0.0   
1               5.666667     0.666667                 0.0             0.0   
2               5.666667     0.666667                 0.0             0.0   
3               0.000000     0.000000                 0.0             0.0   
4               0.000000     0.000000                 0.0             0.0   
...                  ...          ...                 ...             ...   
1262893         0.000000     0.000000                 0.0             0.0   
1262894         0.000000     0.000000                 0.0             0.0   
1262895         0.000000     0.000000                 0.0             0.0   
1262896         0.000000     0.000000                 0.0             0.0   
1262897         0.000000     0.000000                 0.0             0.0   

         fire_cnt_last_year_same_month  fire_last_year_same_month  
0                                  0.0                        0.0  
1                                  0.0                        0.0  
2                                  0.0                        0.0  
3                                  0.0                        0.0  
4                                  0.0                        0.0  
...                                ...                        ...  
1262893                            0.0                        0.0  
1262894                            0.0                        0.0  
1262895                            NaN                        NaN  
1262896                            0.0                        0.0  
1262897                            0.0                        0.0  

[1262898 rows x 13 columns]

In [147]:
X.columns

Index(['latitude', 'longitude', 'common_feature', 'year', 'month',
       'fire_count', 'fire', 'fire_cnt_before', 'fire_before',
       'fire_cnt_last_year', 'fire_last_year', 'fire_cnt_last_year_same_month',
       'fire_last_year_same_month'],
      dtype='object')

In [148]:
X = X.drop(columns='common_feature')

In [149]:
X.head()
X.shape
X.groupby('year').count()

latitude  longitude  year  month  fire_count  fire  fire_cnt_before  \
0      32.4     -117.1  2022      1         3.0     1         5.666667   
1      32.4     -117.1  2022      3        14.0     1         5.666667   
2      32.4     -117.1  2022      2         0.0     0         5.666667   
3      32.4     -117.1  2014      6         0.0     0         0.000000   
4      32.4     -117.1  2003      1         0.0     0         0.000000   

   fire_before  fire_cnt_last_year  fire_last_year  \
0     0.666667                 0.0             0.0   
1     0.666667                 0.0             0.0   
2     0.666667                 0.0             0.0   
3     0.000000                 0.0             0.0   
4     0.000000                 0.0             0.0   

   fire_cnt_last_year_same_month  fire_last_year_same_month  
0                            0.0                        0.0  
1                            0.0                        0.0  
2                            0.0                        0.0  
3                            0.0                        0.0  
4                            0.0                        0.0

(1262898, 12)

latitude  longitude  month  fire_count   fire  fire_cnt_before  \
year                                                                   
2000      9828       9828   9828        9828   9828                0   
2001     58968      58968  58968       58968  58968            58968   
2002     58968      58968  58968       58968  58968            58968   
2003     58968      58968  58968       58968  58968            58968   
2004     58968      58968  58968       58968  58968            58968   
2005     58968      58968  58968       58968  58968            58968   
2006     58968      58968  58968       58968  58968            58968   
2007     58968      58968  58968       58968  58968            58968   
2008     58968      58968  58968       58968  58968            58968   
2009     58968      58968  58968       58968  58968            58968   
2010     58968      58968  58968       58968  58968            58968   
2011     58968      58968  58968       58968  58968            58968   
2012     58968      58968  58968       58968  58968            58968   
2013     58968      58968  58968       58968  58968            58968   
2014     58968      58968  58968       58968  58968            58968   
2015     58968      58968  58968       58968  58968            58968   
2016     58968      58968  58968       58968  58968            58968   
2017     58968      58968  58968       58968  58968            58968   
2018     58968      58968  58968       58968  58968            58968   
2019     58968      58968  58968       58968  58968            58968   
2020     58968      58968  58968       58968  58968            58968   
2021     58968      58968  58968       58968  58968            58968   
2022     14742      14742  14742       14742  14742            14742   

      fire_before  fire_cnt_last_year  fire_last_year  \
year                                                    
2000            0                   0               0   
2001        58968               58968           58968   
2002        58968               58968           58968   
2003        58968               58968           58968   
2004        58968               58968           58968   
2005        58968               58968           58968   
2006        58968               58968           58968   
2007        58968               58968           58968   
2008        58968               58968           58968   
2009        58968               58968           58968   
2010        58968               58968           58968   
2011        58968               58968           58968   
2012        58968               58968           58968   
2013        58968               58968           58968   
2014        58968               58968           58968   
2015        58968               58968           58968   
2016        58968               58968           58968   
2017        58968               58968           58968   
2018        58968               58968           58968   
2019        58968               58968           58968   
2020        58968               58968           58968   
2021        58968               58968           58968   
2022        14742               14742           14742   

      fire_cnt_last_year_same_month  fire_last_year_same_month  
year                                                            
2000                              0                          0  
2001                           9828                       9828  
2002                          58968                      58968  
2003                          58968                      58968  
2004                          58968                      58968  
2005                          58968                      58968  
2006                          58968                      58968  
2007                          58968                      58968  
2008                          58968                      58968  
2009                          58968                      58968  

In [150]:
# 2000 - 2019 - Training Dataset
# 2020 - 2021 - Validation Dataset
# 2022 - Test Dataset
train = X[X.year < 2020].dropna()
valid = X[(X.year >= 2020) & (X.year <= 2021)]
test = X[X.year == 2022]

In [151]:
train.groupby('year').count()
valid.groupby('year').count()
test.groupby('year').count()

latitude  longitude  month  fire_count   fire  fire_cnt_before  \
year                                                                   
2001      9828       9828   9828        9828   9828             9828   
2002     58968      58968  58968       58968  58968            58968   
2003     58968      58968  58968       58968  58968            58968   
2004     58968      58968  58968       58968  58968            58968   
2005     58968      58968  58968       58968  58968            58968   
2006     58968      58968  58968       58968  58968            58968   
2007     58968      58968  58968       58968  58968            58968   
2008     58968      58968  58968       58968  58968            58968   
2009     58968      58968  58968       58968  58968            58968   
2010     58968      58968  58968       58968  58968            58968   
2011     58968      58968  58968       58968  58968            58968   
2012     58968      58968  58968       58968  58968            58968   
2013     58968      58968  58968       58968  58968            58968   
2014     58968      58968  58968       58968  58968            58968   
2015     58968      58968  58968       58968  58968            58968   
2016     58968      58968  58968       58968  58968            58968   
2017     58968      58968  58968       58968  58968            58968   
2018     58968      58968  58968       58968  58968            58968   
2019     58968      58968  58968       58968  58968            58968   

      fire_before  fire_cnt_last_year  fire_last_year  \
year                                                    
2001         9828                9828            9828   
2002        58968               58968           58968   
2003        58968               58968           58968   
2004        58968               58968           58968   
2005        58968               58968           58968   
2006        58968               58968           58968   
2007        58968               58968           58968   
2008        58968               58968           58968   
2009        58968               58968           58968   
2010        58968               58968           58968   
2011        58968               58968           58968   
2012        58968               58968           58968   
2013        58968               58968           58968   
2014        58968               58968           58968   
2015        58968               58968           58968   
2016        58968               58968           58968   
2017        58968               58968           58968   
2018        58968               58968           58968   
2019        58968               58968           58968   

      fire_cnt_last_year_same_month  fire_last_year_same_month  
year                                                            
2001                           9828                       9828  
2002                          58968                      58968  
2003                          58968                      58968  
2004                          58968                      58968  
2005                          58968                      58968  
2006                          58968                      58968  
2007                          58968                      58968  
2008                          58968                      58968  
2009                          58968                      58968  
2010                          58968                      58968  
2011                          58968                      58968  
2012                          58968                      58968  
2013                          58968                      58968  
2014                          58968                      58968  
2015                          58968                      58968  
2016                          58968                      58968  
2017                          58968                      58968  
2018                          58968                      589

latitude  longitude  month  fire_count   fire  fire_cnt_before  \
year                                                                   
2020     58968      58968  58968       58968  58968            58968   
2021     58968      58968  58968       58968  58968            58968   

      fire_before  fire_cnt_last_year  fire_last_year  \
year                                                    
2020        58968               58968           58968   
2021        58968               58968           58968   

      fire_cnt_last_year_same_month  fire_last_year_same_month  
year                                                            
2020                          58968                      58968  
2021                          58968                      58968

latitude  longitude  month  fire_count   fire  fire_cnt_before  \
year                                                                   
2022     14742      14742  14742       14742  14742            14742   

      fire_before  fire_cnt_last_year  fire_last_year  \
year                                                    
2022        14742               14742           14742   

      fire_cnt_last_year_same_month  fire_last_year_same_month  
year                                                            
2022                          14742                      14742

In [152]:
train.to_csv('ca_fire_train.csv', index=False)
valid.to_csv('ca_fire_valid.csv', index=False)
test.to_csv('ca_fire_test.csv', index=False)

In [153]:
train.shape, valid.shape, test.shape
train.head()

((1071252, 12), (117936, 12), (14742, 12))

latitude  longitude  year  month  fire_count  fire  fire_cnt_before  \
3      32.4     -117.1  2014      6         0.0     0              0.0   
4      32.4     -117.1  2003      1         0.0     0              0.0   
5      32.4     -117.1  2015      7         0.0     0              0.0   
6      32.4     -117.1  2019      8         0.0     0              0.0   
7      32.4     -117.1  2005      8         0.0     0              0.0   

   fire_before  fire_cnt_last_year  fire_last_year  \
3          0.0                 0.0             0.0   
4          0.0                 0.0             0.0   
5          0.0                 0.0             0.0   
6          0.0                 0.0             0.0   
7          0.0                 0.0             0.0   

   fire_cnt_last_year_same_month  fire_last_year_same_month  
3                            0.0                        0.0  
4                            0.0                        0.0  
5                            0.0                        0.0  
6                            0.0                        0.0  
7                            0.0                        0.0

In [154]:
# visualization

In [155]:
yearly_fires = history[history.year < 2022].groupby(['year', 'month']).sum().reset_index()

In [156]:
yearly_fires.head()

year  month  latitude  longitude  common_feature  fire_count  fire
0  2000     11  187556.8  -585106.9            4914       271.0   168
1  2000     12  187556.8  -585106.9            4914        78.0    45
2  2001      1  187556.8  -585106.9            4914       108.0    43
3  2001      2  187556.8  -585106.9            4914        69.0    44
4  2001      3  187556.8  -585106.9            4914       181.0   111

In [157]:
px.bar(yearly_fires, x='month', y='fire_count', color='year',
       title='Wildfire Hotspot(months) detections in California')

In [158]:
geo = history.groupby(['latitude', 'longitude']).sum().reset_index()
geo.shape
geo.head()

(4914, 7)

latitude  longitude  common_feature    year  month  fire_count  fire
0      32.4     -117.1             257  516838   1667        17.0     2
1      32.4     -116.9             257  516838   1667        16.0     3
2      32.4     -114.9             257  516838   1667         4.0     2
3      32.4     -114.8             257  516838   1667        28.0     3
4      32.4     -114.6             257  516838   1667         1.0     1

In [159]:
MAPBOX_TOKEN = 'pk.eyJ1IjoiZm9kZ2Fib3JtYXRoIiwiYSI6ImNrZmY3Nzc2bjBiemkyeG8zdGNzcXgzMGIifQ.J0dZhMiuZTPVexL8nrpS6Q'
px.set_mapbox_access_token(MAPBOX_TOKEN)

In [160]:
fig = ff.create_hexbin_mapbox(
    data_frame=geo, lat="latitude", lon="longitude",
    nx_hexagon=50, opacity=0.9, labels={"color": "Hotspot records"},
    color="fire_count", agg_func=np.sum, color_continuous_scale="Reds"
)
fig.show()